# December 17, 2022
https://adventofcode.com/2022/day/17

In [183]:
# Too low: 3132, 3133
# Too high: 5256

# Part 2:
# Too low: 1570434782632

In [184]:
test = ">>><<><>><<<>><>>><<<>>><<<><<<>><>><<>>"

In [1]:
fn = "../data/2022/17.txt"
with open(fn, "r") as file:
    puz = file.readline()

In [186]:
# Tower is oriented [x,y] with [0,0] being left/bottom
class Tower:
    def __init__(self, jets, width=7, retain_rows = 2):
        # Note: bank() method only works for width 4-7!
        # Note: retain_rows must be 2 after more hacking
        self.width = width

        # track which gust comes next
        self.jets = jets
        self.jet_pos = 0

        # instantiate map with floor
        # self.map is recorded from bottom up
        self.map = [ ['-']*self.width ]
        self.height = 0
        self.banked_height = 0
        self.banked_count = [0,0,0,0,0]
        self.retain_rows = retain_rows
        if retain_rows == 0:
            self.banking = False
        else:
            self.banking = True

        # For warping
        self.memo = dict()
        self.nwarp = 0
        self.warped_height = 0
        self.warped_blocks = 0
            
        
        # track current active block
        # 0Flat, Cross, 2Ell, 3Pipe, 4Tuba
        self.next = 0
        self.block_count = 0
        self.spawn_x = 2
        self.spawn_dy = 4
        self.new_block()



    def check(self, x, y):
       # print("Checking",x,y)
        # walls are closed
        if x < 0 or x >= self.width:
            return False

        # open above
        if y > self.height:
            return True

        # otherwise check map
        return  (self.map[y][x]=='.') # using this for blank

    def bank(self, goal):
        if not self.banking:
            return

        if self.height > self.retain_rows:
            #print("Let's try banking")
            # This method works for retain_rows == 3
            # check that each column has at least one block in the top 3 rows
            can_bank = True
            memo_id = 0
            for x in range(self.width):
                col_okay = False
                for y in range(self.height, self.height-self.retain_rows, -1):
                    if not self.check( x, y ):
                        col_okay = True
                        #memo_id = memo_id*2+(self.height-y)
                        memo_id = memo_id*100+x*10+(self.height-y)
                        break
                if not col_okay:
                    can_bank = False
                    break
            
            if can_bank:
                memo_id  = memo_id * 100000 + self.jet_pos
                memo_id = memo_id*10+self.next

                self.banked_count[self.next] += 1
                to_bank = self.height - self.retain_rows
                self.map = self.map[-(1+self.retain_rows):]
                self.height = self.retain_rows
                self.banked_height += to_bank

                if self.block is not None:
                    self.block.y -= to_bank
                    if self.block.y <= 0:
                        self.new_block()

                print("\n")
                print(self)
                print(self.jet_pos, memo_id, self.block_count, self.banked_height)
                
                if memo_id in self.memo.keys() and self.nwarp == 0: # this second condition probably isn't needed
                    # huzzah! ready to warp!                   
                    print("Warping!")
                    print("memo_id:", memo_id)
                    print("cur block_count:", self.block_count)
                    print("cur banked height:", self.banked_height)

                    bc_step = self.block_count - self.memo[memo_id][0]
                    bh_step = self.banked_height - self.memo[memo_id][1]

                    blocks_needed = goal - self.block_count
                    self.nwarp += int(blocks_needed / bc_step )
                    self.warped_height += self.nwarp * bh_step
                    self.warped_blocks += self.nwarp * bc_step
                    self.block_count += self.warped_blocks


                    print("blocks per warp:", bc_step)
                    print("height per warp:", bh_step)
                    print("warps:", self.nwarp)
                    print("warped height:", self.warped_height)
                    print("warped blocks:", self.warped_blocks)
                    print("final block count:", self.block_count)                    
                    
                else:
                    self.memo[memo_id] = [self.block_count, self.banked_height]


            else:
                #print("Can't bank")
                #print(self)
                pass
            return
    

    def new_block(self):
        y = self.height + self.spawn_dy
        if self.next == 0:
            self.block = Flat(self.spawn_x, y, self)
        elif self.next == 1:
            self.block = Cross(self.spawn_x,y, self)
        elif self.next == 2:
            self.block = Ell(self.spawn_x,y, self)
        elif self.next == 3:
            self.block = Pipe(self.spawn_x,y, self)
        elif self.next == 4:
            self.block = Tuba(self.spawn_x,y, self)
        self.next = (self.next + 1) % 5
        self.block_count += 1

    def gust(self):
        jet = self.jets[self.jet_pos]
        if jet == "<":
            if self.block.check_left():
                self.block.x -= 1
        else: # jet == ">":
            if self.block.check_right():
                self.block.x += 1
        self.jet_pos = (self.jet_pos + 1) % len(self.jets)



    def drop(self, goal):
        # return True if block dropped, False if it's stuck
        if self.block.check_down():
            self.block.y -= 1
            if self.block.y == 0: # assume the block falls into oblivion and doesn't affect tower height
                self.new_block()
                return False
            return True
        else:
            pixels = self.block.pixels()
            for xy in pixels:
                self.solidify(xy[0], xy[1], self.block.char)
            self.block = None # needed because otherwise debug printing can mess up the internal representation,
            # being hacky as it is

            # Majority of banking (with retain_rows 2) occurs after type 1 drops (Cross)
            if self.next == 2 or True:
                self.bank(goal)
            self.new_block()
            return False

    def solidify(self, x, y, char):
        # add to tower height as needed
        dy = y - self.height
        for i in range(dy):
            self.map += [ ['.']*self.width ]
            self.height += 1
        self.map[y][x] = char

    def __str__(self):
        addendum = []
        out = []

        if self.block is not None:
            dy = self.block.y + (self.block.height-1) - self.height
            pixels = self.block.pixels()
            for y in range(dy):
                addendum.append( ['.']*self.width )

            for xy in pixels:
                if xy[1] > self.height:
                    # add to addendum
                    y2 = xy[1]-1 - self.height
                    addendum[y2][xy[0]] = '@'
                else:
                    self.map[xy[1]][xy[0]] = '@'

            for line in addendum[::-1]:
                out.append( "".join(line) )
        
        for line in self.map[::-1]:
            out.append( "".join(line) )

        if self.block is not None:
            # reset the map's block spaces
            for xy in pixels:
                if xy[1] <= self.height:
                    self.map[xy[1]][xy[0]] = '.'
                
        return "\n".join(out)
    
    def __repr__(self):
        return self.__str__(self)

class Block:
    pass

class Flat(Block):
    # refpoint is left-most
    def __init__(self, x, y, tower):
        self.x = x
        self.y = y
        self.tower = tower
        self.type = "Flat"
        self.height = 1
        self.char = "A"

    def check_right(self):
        return self.tower.check(self.x+4, self.y)
    def check_left(self):
        return self.tower.check(self.x-1, self.y)
    def check_down(self):
        for x in range(self.x, self.x+4):
            if not self.tower.check(x, self.y-1):
                return False
        return True
    def pixels(self):
        return [ [self.x, self.y], [self.x+1, self.y], [self.x+2, self.y], [self.x+3, self.y] ]

class Cross(Block):
    # refpoint is bottom-left (empty space)
    def __init__(self, x, y, tower):
        self.x = x
        self.y = y
        self.tower = tower
        self.type = "Cross"
        self.height = 3
        self.char = "B"


    def check_right(self):
        return (self.tower.check(self.x+2, self.y)
                and self.tower.check(self.x+3, self.y+1)
                and self.tower.check(self.x+2, self.y+2))
    def check_left(self):
        return (self.tower.check(self.x, self.y)
                and self.tower.check(self.x-1, self.y+1)
                and self.tower.check(self.x, self.y+2))
    def check_down(self):
        return (self.tower.check(self.x, self.y)
                and self.tower.check(self.x+1, self.y-1)
                and self.tower.check(self.x+2, self.y))
    def pixels(self):
        return [ [self.x+1, self.y], [self.x, self.y+1], [self.x+1, self.y+1], [self.x+2, self.y+1], [self.x+1, self.y+2] ]

class Ell(Block):
    # refpoint is bottom-left (empty space)
    def __init__(self, x, y, tower):
        self.x = x
        self.y = y
        self.tower = tower
        self.type = "Ell"
        self.height = 3
        self.char = "C"

    def check_right(self):
        return (self.tower.check(self.x+3, self.y)
                and self.tower.check(self.x+3, self.y+1)
                and self.tower.check(self.x+3, self.y+2))
    def check_left(self):
        return (self.tower.check(self.x-1, self.y)
                and self.tower.check(self.x+1, self.y+1)
                and self.tower.check(self.x+1, self.y+2))
    def check_down(self):
        return (self.tower.check(self.x, self.y-1)
                and self.tower.check(self.x+1, self.y-1)
                and self.tower.check(self.x+2, self.y-1))
    def pixels(self):
        return [ [self.x, self.y], [self.x+1, self.y], [self.x+2, self.y], [self.x+2, self.y+1], [self.x+2, self.y+2] ]

class Pipe(Block):
    # refpoint is bottom-left (empty space)
    def __init__(self, x, y, tower):
        self.x = x
        self.y = y
        self.tower = tower
        self.type = "Pipe"
        self.height = 4
        self.char = "D"


    def check_right(self):
        return (self.tower.check(self.x+1, self.y)
                and self.tower.check(self.x+1, self.y+1)
                and self.tower.check(self.x+1, self.y+2)
                and self.tower.check(self.x+1, self.y+3))
    def check_left(self):
        return (self.tower.check(self.x-1, self.y)
                and self.tower.check(self.x-1, self.y+1)
                and self.tower.check(self.x-1, self.y+2)
                and self.tower.check(self.x-1, self.y+3))
    def check_down(self):
        return self.tower.check(self.x, self.y-1)
    def pixels(self):
        return [ [self.x, self.y], [self.x, self.y+1], [self.x, self.y+2], [self.x, self.y+3] ]

class Tuba(Block): # Two-buh-two
    # refpoint is bottom-left (empty space)
    def __init__(self, x, y, tower):
        self.x = x
        self.y = y
        self.tower = tower
        self.type = "Tuba"
        self.height = 2
        self.char = "E"


    def check_right(self):
        return (self.tower.check(self.x+2, self.y)
                and self.tower.check(self.x+2, self.y+1))
    def check_left(self):
        return (self.tower.check(self.x-1, self.y)
                and self.tower.check(self.x-1, self.y+1))
    def check_down(self):
        return (self.tower.check(self.x, self.y-1)
                and self.tower.check(self.x+1, self.y-1))
    def pixels(self):
        return [ [self.x, self.y], [self.x+1, self.y], [self.x, self.y+1], [self.x+1, self.y+1] ]


In [187]:
import datetime as dt

def play_game( tower, until=2023, verbose=0 ):
    print("Starting...")
    print(dt.datetime.now().isoformat())
    while tower.block_count < until:
        #print(tower.jets[tower.jet_pos], tower.block.type)
        if verbose >= 2:
            print("\n", tower.jets[tower.jet_pos], tower.block.type)
        tower.gust()
        if verbose >= 4:
            print(tower)
        success = tower.drop(until)
        if (not success and verbose >=1) or verbose >= 3:
            print("\n", tower, "\n", sep="")
        if not success and tower.block_count % 1e6 == 0:
            print(f"Done {tower.block_count} blocks!")
            print(dt.datetime.now().isoformat())

### Part 1

In [188]:
test_tower = Tower(test, retain_rows=2)
play_game(test_tower, 2023)
ans = (test_tower.height, test_tower.banked_height, test_tower.warped_height)
print(sum(ans), ans)

Starting...
2022-12-25T21:25:06.528969
3068 (3068, 0, 0)


In [189]:
puz_tower = Tower(puz, retain_rows=2)
play_game(puz_tower, 2023)
part1 = (puz_tower.height, puz_tower.banked_height, puz_tower.warped_height)
print(sum(part1), part1)

Starting...
2022-12-25T21:25:06.679903


AAAAEEC
..D.EEC
..D.CCC
841 102030405060008411 136 215


AAAA.B.
D...BBB
D.EECB.
2941 102030415061029412 502 807


.B.....
BBBAAAA
.BEE...
3946 1102131415161039462 677 1084


.....B.
AAAABBB
..EECB.
4034 1112131415061040342 692 1107


.B.....
BBBAAAA
DBEE...
4819 1102131415161048192 827 1316


...AAAA
EECD...
EECD...
5879 1112130405060058791 1016 1638


AAAA.B.
..EEBBB
.BEECB.
5944 102030415061059442 1027 1651


.B.AAAA
BBB...D
.BEE..D
7997 1102130405060079972 1372 2158


.B.AAAA
BBB..D.
.BEE.D.
9598 1102130405060095982 1637 2586


.....B.
AAAABBB
..EECB.
965 1112131415061009652 1887 2980
3181 (201, 2980, 0)


### Part 1.5

In [203]:
# 5 isn't guaranteed to work, but it does for test tower
test_tower = Tower(test, retain_rows=0)
play_game(test_tower, 250000)
ans = [test_tower.height, test_tower.banked_height, test_tower.warped_height]
print(sum(ans), ans)

Starting...
2022-12-25T21:28:06.972589
378577 [378577, 0, 0]


In [204]:
print(test_tower)

..@@...
..@@...
.......
.......
.......
D......
D......
D.C....
D.C....
CCCB...
..BBB..
...B...
..AAAA.
.EE....
.EE...C
..D...C
..D.CCC
..D..B.
..D.BBB
.AAAAB.
....D..
....D..
....D..
....D..
.EE.C..
.EE.C..
..CCC..
...B...
..BBB..
...B...
..AAAA.
..EEC..
..EEC..
..CCCB.
....BBB
.....B.
.DAAAA.
.D..D..
.D..D..
.DEED.C
.BEED.C
BBB.CCC
.BAAAA.
.DEE...
.DEE...
.D.C...
.D.C.B.
.CCCBBB
.AAAAB.
....D..
....D..
....D..
....D..
.EE.C..
.EE.C..
..CCC..
....B..
...BBB.
D...B..
DAAAA..
D.C....
D.C....
CCCB...
..BBBEE
...B.EE
..AAAA.
.EE....
.EE...C
..D...C
..D.CCC
..D..B.
..D.BBB
.AAAAB.
....D..
....D..
....D..
....D..
.EE.C..
.EE.C..
..CCC..
...B...
..BBB..
...B...
..AAAA.
..EEC..
..EEC..
..CCCB.
....BBB
.....B.
.DAAAA.
.D..D..
.D..D..
.DEED.C
.BEED.C
BBB.CCC
.BAAAA.
.DEE...
.DEE...
.D.C...
.D.C.B.
.CCCBBB
.AAAAB.
....D..
....D..
....D..
....D..
.EE.C..
.EE.C..
..CCC..
....B..
...BBB.
D...B..
DAAAA..
D.C....
D.C....
CCCB...
..BBBEE
...B.EE
..AAAA.
.EE....
.EE...C
..D...C
..D.CCC
..D..B.
..D.BBB


In [205]:
# 5 isn't guaranteed to work, but it does for test tower
test_tower = Tower(test, retain_rows=5)
play_game(test_tower, 250000)
ans = [test_tower.height, test_tower.banked_height, test_tower.warped_height]
print(sum(ans), ans)

Starting...
2022-12-25T21:29:42.803015


......C
.B....C
BBB.CCC
.BAAAA.
.DEE...
.DEE...
36 2112233425260000363 43 65


....D..
....D..
..EED.C
.BEED.C
BBB.CCC
.BAAAA.
10 4132232405462000100 45 67


......C
.B....C
BBB.CCC
.BAAAA.
.DEE...
.DEE...
36 2112233425260000363 78 118
Warping!
memo_id: 2112233425260000363
cur block_count: 78
cur banked height: 118
blocks per warp: 35
height per warp: 53
warps: 7140
warped height: 378420
warped blocks: 249900
final block count: 249978


....D..
....D..
..EED.C
.BEED.C
BBB.CCC
.BAAAA.
10 4132232405462000100 249980 120
378577 [37, 120, 378420]


In [212]:
# 5 isn't guaranteed to work, but it does for test tower
puz_tower = Tower(puz, retain_rows=0)
play_game(puz_tower, 250000)
ans = [puz_tower.height, puz_tower.banked_height, puz_tower.warped_height]
print(sum(ans), ans)

Starting...
2022-12-25T21:34:14.300508
392632 [392632, 0, 0]


In [ ]:
# 5 isn't guaranteed to work, but it does for test tower
puz_tower = Tower(puz, retain_rows=2)
play_game(puz_tower, 250000)
ans = [puz_tower.height, puz_tower.banked_height, puz_tower.warped_height]
print(sum(ans), ans)

Starting...
2022-12-25T21:34:05.079083


AAAAEEC
..D.EEC
..D.CCC
841 102030405060008411 136 215


AAAA.B.
D...BBB
D.EECB.
2941 102030415061029412 502 807


.B.....
BBBAAAA
.BEE...
3946 1102131415161039462 677 1084


.....B.
AAAABBB
..EECB.
4034 1112131415061040342 692 1107


.B.....
BBBAAAA
DBEE...
4819 1102131415161048192 827 1316


...AAAA
EECD...
EECD...
5879 1112130405060058791 1016 1638


AAAA.B.
..EEBBB
.BEECB.
5944 102030415061059442 1027 1651


.B.AAAA
BBB...D
.BEE..D
7997 1102130405060079972 1372 2158


.B.AAAA
BBB..D.
.BEE.D.
9598 1102130405060095982 1637 2586


.....B.
AAAABBB
..EECB.
965 1112131415061009652 1887 2980


AAAA.B.
D...BBB
D.EECB.
2941 102030415061029412 2227 3516
Warping!
memo_id: 102030415061029412
cur block_count: 2227
cur banked height: 3516
blocks per warp: 1725
height per warp: 2709
warps: 143
warped height: 387387
warped blocks: 246675
final block count: 248902


.B.....
BBBAAAA
.BEE...
3946 1102131415161039462 249077 3793


.....B.
AAAABBB
..EECB.
4034 1

In [214]:
# 5 isn't guaranteed to work, but it does for test tower
puz_tower = Tower(puz, retain_rows=5)
play_game(puz_tower, 250000)
ans = [puz_tower.height, puz_tower.banked_height, puz_tower.warped_height]
print(sum(ans), ans)

Starting...
2022-12-25T21:37:17.343599


...AAAA
EE.C...
EE.C...
.CCC.D.
...B.D.
..BBBD.
32 1112330405060000321 6 3


...B...
..BBB..
...B...
...AAAA
EE.C...
EE.C...
36 4142130415363000362 7 6


AAAA...
..EE...
..EE...
..D..B.
..D.BBB
..D.CB.
252 102030445364002522 42 71


......C
.B....C
BBB.CCC
.B..D..
AAAAD..
..EEDC.
659 2112234425260006593 103 158


AAAAEEC
..D.EEC
..D.CCC
..D..B.
..D.BBB
.AAAAB.
841 102030405060008411 136 212


....B..
...BBB.
....B..
AAAAEEC
..D.EEC
..D.CCC
845 3132331405163008452 137 215


..C.B..
..CBBB.
CCC.B.C
..AAAAC
D.EECCC
D.EEB..
885 2122031405162008853 143 220


.....C.
.B...C.
BBBCCC.
.BAAAA.
....EED
....EED
1022 2112232425064010224 169 271


AAAA...
..EE..C
..EE..C
...BCCC
..BBB..
...B...
1063 102030435361010631 176 280


......C
.B....C
BBB.CCC
.BAAAA.
..D....
..D.EE.
1233 2112233425260012333 208 331


..D....
..D....
..DEE.C
.BDEE.C
BBB.CCC
.BAAAA.
1247 4132032425462012470 210 333


......C
.B....C
BBB.CCC
.BAAAA.
..D....
..D....
1262 211223342526001

In [ ]:
print(puz_tower)

### Part 2

In [216]:
# 5 isn't guaranteed to work, but it does for test tower
test_tower = Tower(test, retain_rows=5)
play_game(test_tower, 1e12+1)
ans = [test_tower.height, test_tower.banked_height, test_tower.warped_height]
print(sum(ans), ans)

Starting...
2022-12-25T21:38:49.350675


......C
.B....C
BBB.CCC
.BAAAA.
.DEE...
.DEE...
36 2112233425260000363 43 65


....D..
....D..
..EED.C
.BEED.C
BBB.CCC
.BAAAA.
10 4132232405462000100 45 67


......C
.B....C
BBB.CCC
.BAAAA.
.DEE...
.DEE...
36 2112233425260000363 78 118
Warping!
memo_id: 2112233425260000363
cur block_count: 78
cur banked height: 118
blocks per warp: 35
height per warp: 53
warps: 28571428569
warped height: 1514285714157
warped blocks: 999999999915
final block count: 999999999993


....D..
....D..
..EED.C
.BEED.C
BBB.CCC
.BAAAA.
10 4132232405462000100 999999999995 120
Done 1000000000000 blocks!
2022-12-25T21:38:49.354670
1514285714288 [11, 120, 1514285714157]


In [217]:
puz_tower = Tower(puz, retain_rows=2)
play_game(puz_tower, 1e12+1) # <-- lol... spent a decent hour figuring out that +1
ans = [puz_tower.height, puz_tower.banked_height, puz_tower.warped_height]
print(sum(ans), ans)

Starting...
2022-12-25T21:39:00.484727


AAAAEEC
..D.EEC
..D.CCC
841 102030405060008411 136 215


AAAA.B.
D...BBB
D.EECB.
2941 102030415061029412 502 807


.B.....
BBBAAAA
.BEE...
3946 1102131415161039462 677 1084


.....B.
AAAABBB
..EECB.
4034 1112131415061040342 692 1107


.B.....
BBBAAAA
DBEE...
4819 1102131415161048192 827 1316


...AAAA
EECD...
EECD...
5879 1112130405060058791 1016 1638


AAAA.B.
..EEBBB
.BEECB.
5944 102030415061059442 1027 1651


.B.AAAA
BBB...D
.BEE..D
7997 1102130405060079972 1372 2158


.B.AAAA
BBB..D.
.BEE.D.
9598 1102130405060095982 1637 2586


.....B.
AAAABBB
..EECB.
965 1112131415061009652 1887 2980


AAAA.B.
D...BBB
D.EECB.
2941 102030415061029412 2227 3516
Warping!
memo_id: 102030415061029412
cur block_count: 2227
cur banked height: 3516
blocks per warp: 1725
height per warp: 2709
warps: 579710143
warped height: 1570434777387
warped blocks: 999999996675
final block count: 999999998902


.B.....
BBBAAAA
.BEE...
3946 1102131415161039462 999999999077 3793



In [ ]:
print(puz_tower)

In [209]:
puz_tower.memo

{102030405060008411: [136, 215],
 102030415061029412: [502, 807],
 1102131415161039462: [999999999077, 3793],
 1112131415061040342: [999999999092, 3816],
 1102131415161048192: [999999999227, 4025],
 1112130405060058791: [999999999416, 4347],
 102030415061059442: [999999999427, 4360],
 1102130405060079972: [999999999772, 4867],
 1102130405060095982: [1637, 2586],
 1112131415061009652: [1887, 2980]}